<a href="https://colab.research.google.com/github/dataforgoodfr/batch7_satellite_ges/blob/master/notebooks/WIP_OCO2_Capture.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
!pip install --user python-swiftclient python-keystoneclient --upgrade
!apt-get install swiftclient

from google.colab import drive
drive.mount('/content/drive')

In [0]:
import swiftclient
import json
with open("/content/drive/My Drive/Data For Good - S7: Ministère & O-CO2/config.json") as json_data_file:
    config = json.load(json_data_file)
#print(config['swift_storage']['user'])

def swift_con(config):
    user=config['swift_storage']['user']
    key=config['swift_storage']['key']
    auth_url=config['swift_storage']['auth_url']
    tenant_name=config['swift_storage']['tenant_name']
    auth_version=config['swift_storage']['auth_version']
    options = config['swift_storage']['options']
    return swiftclient.Connection(user=user,
                                  key=key,
                                  authurl=auth_url,
                                  os_options=options,
                                  tenant_name=tenant_name,
                                  auth_version=auth_version)

conn = swift_con(config)

In [0]:
# Test
for container in conn.get_account()[1]:
    container_name = container['name']
    print('container_name:', container_name)
objects = conn.get_container(container_name)[1]
for data in objects:
    if 'oco2_1504' in data['name']:
        print('{0}\t{1}\t{2}'.format(data['name'], data['bytes'], data['last_modified']))

container_name: oco2
/datasets/oco-2/peaks-detected/result_for_oco2_1504.csv	21241	2020-05-05T17:13:30.884370
/datasets/oco-2/soudings/oco2_1504.csv.xz	75186100	2020-05-03T07:48:47.793680


# OCO2 - Visualize detected peaks and other sources

Project for **Data For Good**, season 7. 

---

## Introduction

Using Data from [OCO-2 Satellite](en.wikipedia.org/wiki/Orbiting_Carbon_Observatory_2), issued by the NASA.

We here try to reproduce the results from [this paper](https://www.atmos-chem-phys-discuss.net/acp-2020-123/) by F. Chevallier, trying to "[observe] carbon dioxide emissions over China's cities with the Orbiting Carbon Observatory-2".

`//TODO: Explanation`

In [0]:
import pandas as pd
import numpy as np
from numpy import exp, loadtxt, pi, sqrt
import matplotlib
import matplotlib.pyplot as plt
import seaborn as sns
from io import StringIO
import folium
from folium import plugins

/usr/local/lib/python3.6/dist-packages/statsmodels/tools/_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


## Show Data on the map

##### **haversine**: Function to calculate the great circle distance between two points on the earth given longitude and latitude.

*Parameters*: 

*   (int) **lon1** : the longitude of the first point.
*   (int) **lon2**: the latitude of the first point.
*   (int) **lat1**: the longitude of the second point.
*   (int) **lat2**: the latitude of the second point.

*Return:*


*   (int) the distance (in kilometers)

In [0]:
from math import radians, cos, sin, asin, sqrt

def haversine_formula(lon1, lat1, lon2, lat2):
    # convert decimal degrees to radians 
    lon1, lat1, lon2, lat2 = map(radians, [lon1, lat1, lon2, lat2])

    # haversine formula 
    dlon = lon2 - lon1 
    dlat = lat2 - lat1 
    a = sin(dlat/2)**2 + cos(lat1) * cos(lat2) * sin(dlon/2)**2
    c = 2 * asin(sqrt(a)) 
    r = 6371 # Radius of earth in kilometers. Use 3956 for miles
    return c * r

def haversine(row, lat, lon):
    return haversine_formula(lon, lat, row['longitude'], row['latitude'])

In [0]:
# http://courty.fr/OCO2/peak_data-f_oco2_1808-o_21733-si_2018080216413233.json

def load_one_peak_data(sounding_id, df_all_peak):
    df_param = df_all_peak.query("sounding_id==@sounding_id")
    param_index = df_param.index[0]
    url = input_dir + "peak_data-f_oco2_1808-o_"+str(df_param.loc[param_index, 'orbit'])+"-si_"+sounding_id+".json"
    print(url)
    df_peak = pd.read_json(url)
    
    gaussian_param = {
        'slope' : df_param.loc[param_index, 'slope'],
        'intercept' : df_param.loc[param_index, 'intercept'],
        'amplitude' : df_param.loc[param_index, 'amplitude'],
        'sigma': df_param.loc[param_index, 'sigma'],
        'delta': df_param.loc[param_index, 'delta'],
        'R' : df_param.loc[param_index, 'R'],
    }
    return df_peak, gaussian_param

'''
x : the data input value
m : the slope of the data
b : the intercep of the data
A : Amplitude de la courbe
sig : sigma / écart type de la courbe
'''
def gaussian(x, m, b, A, sig):
    return m * x + b + A / (sig * (2 * np.pi)**0.5) * np.exp(-x**2 / (2*sig**2))

def plot_peak(df_peak, gaussian_param):
    x = df_peak['distance']
    y = df_peak['xco2']
    y = y - gaussian_param['slope'] * x - gaussian_param['intercept']
    plt.scatter(x, y, c=y, s=3, label='sounding')
    plt.plot(x, gaussian(x, m=0, b=0, A=gaussian_param['amplitude'], sig=gaussian_param['sigma']), 'r', label='fit')
    plt.legend()
    plt.title('OCO 2 data')
    plt.xlabel('Distance')
    plt.ylabel('CO²')
    plt.show()

---

## Retieve Data

Sample data can be accessed freely on the NASA Database, among other open data from several NASA sattelites.

### First Peak Detection

In [0]:
csv = conn.get_object("oco2", "/datasets/oco-2/peaks-detected/result_for_oco2_1808.csv")[1]
peak_fc = pd.read_csv(StringIO(str(csv, 'utf-8')))

peak_fc.head()

Unnamed: 0       sounding_id  ...  land_water_indicator  land_fraction
0           0  2018080101035604  ...                   1.0            0.0
1           1  2018080101062035  ...                   1.0            0.0
2           2  2018080101062937  ...                   1.0            0.0
3           3  2018080111005177  ...                   0.0          100.0
4           4  2018080220003337  ...                   0.0          100.0

[5 rows x 18 columns]

We spot some negative sigma and amplitude parameters.

In [0]:
peak_fc['sigma'] = peak_fc['sigma'].apply(abs)
peak_fc['amplitude'] = peak_fc['amplitude'].apply(abs)
peak_fc.describe()

Unnamed: 0   sounding_id  ...  land_water_indicator  land_fraction
count  190.000000  1.900000e+02  ...            190.000000     190.000000
mean    94.500000  2.018082e+15  ...              0.236842      80.810526
std     54.992424  9.053339e+08  ...              0.526253      39.225652
min      0.000000  2.018080e+15  ...              0.000000       0.000000
25%     47.250000  2.018081e+15  ...              0.000000     100.000000
50%     94.500000  2.018082e+15  ...              0.000000     100.000000
75%    141.750000  2.018083e+15  ...              0.000000     100.000000
max    189.000000  2.018083e+15  ...              3.000000     100.000000

[8 rows x 18 columns]

To convert the  ``` sounding_id ``` into a datetime variable ```date```:



In [0]:
from datetime import datetime
def to_date(a):
    return datetime.strptime(str(a), '%Y%m%d%H%M%S%f')

peak_fc['date'] = peak_fc['sounding_id'].apply(to_date)
peak_fc.head()

Unnamed: 0       sounding_id  ...  land_fraction                    date
0           0  2018080101035604  ...            0.0 2018-08-01 01:03:56.040
1           1  2018080101062035  ...            0.0 2018-08-01 01:06:20.350
2           2  2018080101062937  ...            0.0 2018-08-01 01:06:29.370
3           3  2018080111005177  ...          100.0 2018-08-01 11:00:51.770
4           4  2018080220003337  ...          100.0 2018-08-02 20:00:33.370

[5 rows x 19 columns]

### LOF & DBSCAN Filtered Peaks

In [0]:
# Charlotte & Raphaele's method
peak_cr = pd.read_csv("https://raw.githubusercontent.com/dataforgoodfr/batch7_satellite_ges/master/dataset/output/peaks_out_1808.csv", sep=",", index_col=0)
peak_cr.describe()

latitude  ...  y_class_dbscan_only_gaussian_param
count  2739.000000  ...                         2739.000000
mean     20.739139  ...                            0.900694
std      26.381097  ...                            0.434534
min     -40.021149  ...                           -1.000000
25%      -3.200449  ...                            1.000000
50%      29.949741  ...                            1.000000
75%      40.669176  ...                            1.000000
max      72.424393  ...                            1.000000

[8 rows x 21 columns]

### Cities estimates

In [0]:
path_cities = "https://raw.githubusercontent.com/dataforgoodfr/batch7_satellite_ges/master/dataset/cities_v1.csv"

cities = pd.read_csv(path_cities, sep=",", index_col=0)

cities.head()

City name   Country  ...   latitude   longitude
0           Toronto    Canada  ...  43.653226  -79.383184
1  Santiago de Cali  Colombia  ...   3.451647  -76.531985
4            Milano     Italy  ...  45.802578    9.086356
5           Hayward       USA  ...  37.668900 -122.080800
6             Tokyo     Japan  ...  35.689634  139.692101

[5 rows x 11 columns]

### EDGAR sources

In [0]:
path_Edgar_2018 = "/content/drive/My Drive/Data For Good - S7: Ministère & O-CO2/data/edgar/CO2_emissions_Edgar_2018_v3.csv"

edgar = pd.read_csv(path_Edgar_2018, sep=",", index_col=0)

# We only keep the 75% highest registered emitters
edgar_top = edgar[edgar['CO2 classification encoded'] > 2]
edgar_top.describe()

# Because there's too much to visualize, we keep only the N highest emissions
N = 1500
count = edgar_top.shape[0]
edgar_top_sample = edgar_top[count-N:count]
edgar_top_sample.describe()

/usr/local/lib/python3.6/dist-packages/numpy/lib/arraysetops.py:569: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  mask |= (ar1 == a)


latitude    longitude  CO2 emissions  CO2 classification encoded
count  1500.000000  1500.000000    1500.000000                      1500.0
mean     33.947200    57.953400       0.000003                         3.0
std      15.471291    76.752384       0.000005                         0.0
min     -38.150002  -151.250000       0.000001                         3.0
25%      28.125000    20.200000       0.000002                         3.0
50%      35.549999    98.600002       0.000002                         3.0
75%      41.250000   116.974998       0.000004                         3.0
max      69.349998   152.050003       0.000121                         3.0

---

### Power Plants sources

In [0]:
path_plants = "https://raw.githubusercontent.com/dataforgoodfr/batch7_satellite_ges/master/dataset/CO2_emissions_centrale.csv"

plants = pd.read_csv(path_plants, sep=",", index_col=0)

plants.head()

country_long  ...  tCO2_emitted_in_2017_with estimated_data
0  Afghanistan  ...                                       NaN
1      Algeria  ...                              9.534467e+05
2      Algeria  ...                              1.301821e+05
3      Algeria  ...                              1.026789e+06
4      Algeria  ...                              1.833551e+05

[5 rows x 19 columns]

## Map Visualization

### Inventory Map

In [0]:
# Initialize Map
inventory_map = folium.Map([43, 0], zoom_start=4)
folium.TileLayer("CartoDB dark_matter", name="Dark mode").add_to(inventory_map)

# Adding EDGAR top
edgar_group = folium.FeatureGroup(name="Edgar").add_to(inventory_map)
for index, row in edgar_top_sample.iterrows():
    radius = row['CO2 emissions']*1000000
    color="#50C878" # green

    ''' Add popup and tooltip
    tooltip =  "["+str(round(row['latitude'],2))+" ; "+str(round(row['longitude'],2))+"]"
    emit = str(round(row['CO2 emissions']*1000000,2))
    popup_html="""<h4>"""+tooltip+"""</h4><p><b>CO2 emissions:</b> """+emit+""" (10e-06)</p>"""
    popup=folium.Popup(popup_html, max_width=450)
    '''

    edgar_group.add_child(folium.CircleMarker(location=(row["latitude"],
                                  row["longitude"]),
                        radius=radius,
                        color=color,
                        fill=True))


# Adding Power plants
plants_group = folium.FeatureGroup(name="Plants").add_to(inventory_map)
for index, row in plants.iterrows():
    radius = row['estimated_generation_gwh']/10000
    color="#3186CC" # blue

    ''' Add popup and tooltip
    tooltip =  "["+str(round(row['latitude'],2))+" ; "+str(round(row['longitude'],2))+"]"
    emit = str(round(row['estimated_generation_gwh'],2))
    popup_html="""<h4>"""+tooltip+"""</h4>"""+row['country_long']+"""<p><b>Emission 2018 (est):</b> """+emit+""" GWh</p>"""
    popup=folium.Popup(popup_html, max_width=450)
    '''

    plants_group.add_child(folium.CircleMarker(location=(row["latitude"],
                                  row["longitude"]),
                        radius=radius,
                        color=color,
                        fill=True))


# Adding Cities
cities_group = folium.FeatureGroup(name="Cities").add_to(inventory_map)
for index, row in cities.iterrows():
    radius = row['Population (CDP)']/2000000
    color="#FEF65B" # yellow

    ''' Add popup and tooltip
    tooltip =  "["+str(round(row['latitude'],2))+" ; "+str(round(row['longitude'],2))+"]"
    pop = str(round(row['Population (CDP)'],0))
    title = "" + str(row['City name']) + ", " + str(row['Country'])
    popup_html="""<h4><b>"""+row["City name"]+"""</b>, """+row["Country"]+"""</h4>"""+"""<p>"""+tooltip+"""</p>"""+"""<p>Population 2017: """+pop+"""</p>"""
    popup_html = """<h4>"""+title+"""</h4><p>"""+tooltip+"""</p>"""+"""<p><b>Population 2017:</b> """+pop+"""</p>"""
    popup=folium.Popup(popup_html, max_width=450)
    '''

    cities_group.add_child(folium.CircleMarker(location=(row["latitude"],
                                  row["longitude"]),
                        radius=radius,
                        color=color,
                        fill=True))


folium.map.LayerControl(collapsed=False).add_to(inventory_map)

plugins.Fullscreen(
    position='topright',
    title='Expand me',
    title_cancel='Exit me',
    force_separate_button=True
).add_to(inventory_map)

minimap = plugins.MiniMap()
inventory_map.add_child(minimap)

inventory_map.save("inventory_map.html")
inventory_map

### Map Plot to compare peak detection techniques

In [0]:
# Initialize Map
peaks_methods = folium.Map([43, 0], zoom_start=4)
folium.TileLayer("CartoDB dark_matter", name="Dark mode").add_to(peaks_methods)

# Adding detected peaks
peaks_group = folium.FeatureGroup(name="Peaks").add_to(peaks_methods)
for index, row in data.iterrows():
    radius = row["amplitude"]/20
    color="#FF3333" # red
    
    peaks_group.add_child(folium.CircleMarker(location=(row["latitude"],
                                  row["longitude"]),
                        radius=radius,
                        color=color,
                        fill=True))


# Adding LOF detected peaks
lof_group = folium.FeatureGroup(name="LOF detection").add_to(peaks_methods)
for index, row in peak_cr.iterrows():
    if (row['y_class_lof_only_gaussian_param'] < 0):
      radius = row["amplitude"]/20
      color="#FF66CC" # pink
      
      lof_group.add_child(folium.CircleMarker(location=(row["latitude"],
                                    row["longitude"]),
                          radius=radius,
                          color=color,
                          fill=True))

# Adding DBSCAN detected peaks
dbscan_group = folium.FeatureGroup(name="DBSCAN detection").add_to(peaks_methods)
for index, row in peak_cr.iterrows():
    if (row['y_class_dbscan_only_gaussian_param'] < 0):
      radius = row["amplitude"]/20
      color="#6A287E" # purple

      dbscan_group.add_child(folium.CircleMarker(location=(row["latitude"],
                                    row["longitude"]),
                          radius=radius,
                          color=color,
                          fill=True))


folium.map.LayerControl(collapsed=False).add_to(peaks_methods)

plugins.Fullscreen(
    position='topright',
    title='Expand me',
    title_cancel='Exit me',
    force_separate_button=True
).add_to(peaks_methods)

minimap = plugins.MiniMap()
peaks_methods.add_child(minimap)

peaks_methods.save("peaks_methods.html")
peaks_methods

### Map with "Capture Zone"

In [0]:
import geopy
from geopy.distance import VincentyDistance

def get_direction_from_uv(u, v):
    direction = 180/math.pi * math.atan2(u,v)+180
    return direction

def get_wind_norm_from_uv(u, v):
    return math.sqrt(pow(u,2)+pow(v,2))

def get_new_coord(lat, lon, d, b):
    origin = geopy.Point(lat, lon)
    point = VincentyDistance(kilometers=d).destination(origin, b)
    return [point[0], point[1]]

def capture_zone(lat, lon, u, v, angle=50):
    wind_heading = get_direction_from_uv(u, v)
    wind_norm = get_wind_norm_from_uv(u,v)*3.6

    # BACK LINE
    # 1st point (back - 6h wind)
    point_1 = get_new_coord(lat, lon, wind_norm*6, wind_heading+180)
    # 2nd point (back - 6h wind - 50°)
    point_2 = get_new_coord(lat, lon, wind_norm*6, wind_heading+180-angle)
    # 3rd point (back - 6h wind - 50°)
    point_3 = get_new_coord(lat, lon, wind_norm*6, wind_heading+180+angle)

    # FRONT LINE
    # 4th point (front - 24h wind - 20°)
    point_4 = get_new_coord(lat, lon, wind_norm*24, wind_heading+angle)
    # 5th point (front - 24h wind - 20°)
    point_5 = get_new_coord(lat, lon, wind_norm*24, wind_heading-angle)
    # 6th point (front - 24h wind)
    point_6 = get_new_coord(lat, lon, wind_norm*24, wind_heading)

    points = [point_1, point_2, point_4, point_6, point_5, point_3, point_1]
    return points

In [0]:
# Initialize Map
peaks_capture = folium.Map([43, 0], zoom_start=4)
folium.TileLayer("CartoDB dark_matter", name="Dark mode").add_to(peaks_capture)

# Adding detected peaks
peaks_group = folium.FeatureGroup(name="Peaks").add_to(peaks_capture)
peaks_group_capture = folium.FeatureGroup(name=" - 50km CirclesCapture Zone").add_to(peaks_capture)
for index, row in peak_fc.iterrows():
    radius = row["amplitude"]/20
    color="#FF3333" # red
    sounding = str(row['sounding_id'])
    date = str(row['date'])
    orbit = str(row['orbit'])
    capture = capture_zone(row["latitude"], row["longitude"], row['windspeed_u'], row['windspeed_v'])    
    
    peaks_group.add_child(folium.CircleMarker(location=(row["latitude"],
                                  row["longitude"]),
                        radius=radius,
                        color=color,
                        tooltip=sounding,
                        fill=True))
    
    peaks_group_capture.add_child(folium.PolyLine(capture, color='#B2B2B2', weight = 1))

folium.map.LayerControl(collapsed=False).add_to(peaks_capture)

plugins.Fullscreen(
    position='topright',
    title='Expand me',
    title_cancel='Exit me',
    force_separate_button=True
).add_to(peaks_capture)

minimap = plugins.MiniMap()
peaks_capture.add_child(minimap)

peaks_capture.save("peaks_capture.html")
peaks_capture

## Map Utils

Create map with inventory data only

In [0]:
# Initialize Map
current_map = folium.Map([43, 0], zoom_start=4)
folium.TileLayer("CartoDB dark_matter", name="Dark mode").add_to(current_map)


# ------
#
# Add peaks viz block here
#
# ------


# Adding EDGAR top
edgar_group = folium.FeatureGroup(name="Edgar").add_to(current_map)
for index, row in edgar_top_sample.iterrows():
    radius = row['CO2 emissions']*1000000
    color="#50C878" # green
    tooltip =  "["+str(round(row['latitude'],2))+" ; "+str(round(row['longitude'],2))+"]"
    emit = str(round(row['CO2 emissions']*1000000,2))

    popup_html="""<h4>"""+tooltip+"""</h4><p><b>CO2 emissions:</b> """+emit+""" (10e-06)</p>"""

    popup=folium.Popup(popup_html, max_width=450)
    
    edgar_group.add_child(folium.CircleMarker(location=(row["latitude"],
                                  row["longitude"]),
                        radius=radius,
                        color=color,
                        tooltip=tooltip,
                        popup = popup,
                        fill=True))


# Adding Power plants
plants_group = folium.FeatureGroup(name="Plants").add_to(current_map)
for index, row in plants.iterrows():
    radius = row['estimated_generation_gwh']/10000
    color="#3186CC" # blue
    tooltip =  "["+str(round(row['latitude'],2))+" ; "+str(round(row['longitude'],2))+"]"
    emit = str(round(row['estimated_generation_gwh'],2))
    popup_html="""<h4>"""+tooltip+"""</h4>"""+row['country_long']+"""<p><b>Emission 2018 (est):</b> """+emit+""" GWh</p>"""

    popup=folium.Popup(popup_html, max_width=450)

    plants_group.add_child(folium.CircleMarker(location=(row["latitude"],
                                  row["longitude"]),
                        radius=radius,
                        color=color,
                        tooltip=tooltip,
                        popup=popup,
                        fill=True))


# Adding Cities
cities_group = folium.FeatureGroup(name="Cities").add_to(current_map)
for index, row in cities_top.iterrows():
    radius = row['Population (CDP)']/2000000
    color="#FEF65B" # yellow
    tooltip =  "["+str(round(row['latitude'],2))+" ; "+str(round(row['longitude'],2))+"]"
    pop = str(round(row['Population (CDP)'],0))
    title = "" + str(row['City name']) + ", " + str(row['Country'])
    popup_html="""<h4><b>"""+row["City name"]+"""</b>, """+row["Country"]+"""</h4>"""+"""<p>"""+tooltip+"""</p>"""+"""<p>Population 2017: """+pop+"""</p>"""

    popup_html = """<h4>"""+title+"""</h4><p>"""+tooltip+"""</p>"""+"""<p><b>Population 2017:</b> """+pop+"""</p>"""

    popup=folium.Popup(popup_html, max_width=450)

    cities_group.add_child(folium.CircleMarker(location=(row["latitude"],
                                  row["longitude"]),
                        radius=radius,
                        color=color,
                        tooltip=tooltip,
                        popup=popup,
                        fill=True))


folium.map.LayerControl(collapsed=False).add_to(current_map)

plugins.Fullscreen(
    position='topright',
    title='Expand me',
    title_cancel='Exit me',
    force_separate_button=True
).add_to(current_map)

minimap = plugins.MiniMap()
current_map.add_child(minimap)

current_map.save("current_map.html")
current_map

Add a Peak layer to the map

In [0]:
# With 'data' being the peak dataset
for index, row in data.iterrows():
    # Set peak radius here
    radius = row["amplitude"]/20
    # Set the color here
    color='#FF3333'
    # Set all popup and toolip info here
    tooltip =  "["+str(round(row['latitude'],2))+" ; "+str(round(row['longitude'],2))+"]"
    sounding = str(row['sounding_id'])
    date = str(row['date'])
    orbit = str(row['orbit'])
    popup_html="""<h4>"""+tooltip+"""</h4>"""+date+"""<p>sounding_id: """+sounding+"""</br>orbit: """+orbit+"""</p>"""
    popup=folium.Popup(popup_html, max_width=450)
    
    peaks_group = folium.FeatureGroup(name="Peaks").add_to(my_map)
    peaks_group.add_child(folium.CircleMarker(location=(row["latitude"],
                                 row["longitude"]),
                        radius=radius,
                        color=color,
                        tooltip=tooltip,
                        popup=popup,
                        fill=True))
    
    # Ajouter Capture
    capture = capture_zone(row["latitude"], row["longitude"], row['windspeed_u'], row['windspeed_v'])
    peaks_group_capture = folium.FeatureGroup(name="Peaks 50km Circles").add_to(my_map)
    peaks_group_capture.add_child(folium.PolyLine(capture, color='#B2B2B2', weight = 1))
